# Note
發現在解析心情時會出錯，需要安排時間 debug

# 載入套件

In [2]:
import os
import re
import json
import time
import datetime
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup

# 開發區

## 獲取 PageID

In [2]:
def get_pageid(PageUrl):
    resp = requests.get(PageUrl)
    pageid = re.findall('page_id=(.*?)"',resp.text)[0]
    return pageid

In [3]:
get_pageid('https://www.facebook.com/polin66666')

'102764756435823'

## 貼文

### request資料

In [4]:
PageUrl = 'https://www.facebook.com/polin66666'
PageUrl = 'https://www.facebook.com/tsaiingwen'
PageID = get_pageid(PageUrl)
timeline_cursor = ''
max_date =  datetime.datetime.now()
break_times = 0
content_df = [] # 貼文內容
feedback_df = [] # 心情內容

url = 'https://www.facebook.com/pages_reaction_units/more/'
params = {'page_id': PageID ,
          'cursor': str({"timeline_cursor":timeline_cursor,
                         "timeline_section_cursor":'{}',
                         "has_next_page":'true'}),
          'surface': 'www_pages_home',
          'unit_count': 20,
          '__a': '1'}
resp = requests.get(url, params=params)

In [5]:
data = json.loads(re.sub(r'for \(;;\);','',resp.text))
data.keys()

dict_keys(['__ar', 'payload', 'domops', 'jsmods', 'hsrp', 'allResources', 'lid'])

### 貼文內容
- 貼文姓名、貼文人ID、貼文ID、時間、內容

In [6]:
soup = BeautifulSoup(data['domops'][0][3]['__html'])
soup.findAll('div', {'class':'userContentWrapper'})[0]

<div class="_5pcr userContentWrapper" data-ft='{"tn":"-R"}' style=""><div class="_1dwg _1w_m _q7o" data-visualcompletion="ignore-dynamic"><div></div><div class="_4r_y"><div class="_1wbl" id="u_x7o5vo_1i_AU"></div></div><div><div class="l_c3pyo2v0u _5eit i_c3pynyi2f clearfix"><div class="clearfix y_c3pyo2ta3"><a aria-hidden="true" class="_5pb8 o_c3pynyi2g _8o _8s lfloat _ohe" data-ft='{"tn":"\u003C"}' href="https://www.facebook.com/tsaiingwen/?ref=nf&amp;hc_ref=ARRKFi01_H1Moa6qa28YayNBMHkeVpVllDrmggEOxYswhbAAiDjephcDbQISiBySDck" tabindex="-1" target=""><div class="_38vo"><noscript id="u_x7o5vo_3m_ts"></noscript><div><img alt="" aria-label="蔡英文 Tsai Ing-wen" class="_s0 _4ooo _5xib _5sq7 _44ma _rw img" role="img" src="https://scontent.ftpe7-1.fna.fbcdn.net/v/t1.6435-1/cp0/p50x50/139964342_10157244375646065_4666784625909449327_n.png?_nc_cat=1&amp;ccb=1-3&amp;_nc_sid=dbb9e7&amp;_nc_ohc=BMjoKv4L_tsAX_Zgbhs&amp;_nc_ht=scontent.ftpe7-1.fna&amp;_nc_tp=30&amp;oh=a0a17107aa9b13569bf501fb5f900a5b&

In [7]:
soup.findAll('div', {'class':'userContentWrapper'})[0].find('div',{'data-testid':'post_message'}).text

'非常遺憾，在連假第一天就發生事故，造成重大傷亡，我和國人同感哀傷。 \u3000\u3000 今天上午我接獲通報後，就和 蘇貞昌 院長進行討論，並指示相關單位積極應變。林佳龍、徐國勇兩位部長及蘇院長，已經先後趕到花蓮，稍早我則是來到應變中心，了解救難和後續處置情形。 \u3000\u3000 整起事故，目前還在傾全力搶救的階段，我聽取應變中心簡報後，做出四個指示，也要向大家說明：⋯⋯ \u3000\u3000 1️⃣我們會持續盡全力來搶救：在事故發生後，第一時間就成立一級災害應變中心和前進指揮所，統整所有搶救事務。目前消防、警察、空勤等各單位都積極投入救難，也指示國軍來支援。另外，謝謝許多縣市派遣搜救隊趕赴花蓮。救難第一，我們要請所有參與救難的同仁持續努力。 \u3000\u3000 2️⃣我們會全力協助死傷者家屬：衛福部已啟動「大量傷病患緊急醫療救護機制」，各醫療院所正全力救治傷患。對於不幸罹難的乘客，也請相關單位務必全力協助家屬處理後事。 \u3000\u3000 3️⃣我們會在最短時間內調度搶修交通：連假東部運輸需求大，交通部會積極因應，透過各種方式協助接駁旅客、搶修鐵道。如果因此發生延誤，也希望旅客能體諒。 \u3000\u3000 4️⃣我們會徹查事故原因：嚴重事故造成多人傷亡、台鐵年輕駕駛殉職，國人都相當悲痛。我們已經要求運安會嚴格進行事故調查，完整釐清事故原因後，向各界公開說明。在真相充分釐清前，也希望不要有過度的揣測或指控。 \u3000\u3000 這些任務，我請各相關單位一定要全力以赴。最後，祈願罹難者安息，傷者早日康復。 查看更多'

In [8]:
soup.find('div',{'data-testid':'story-subtitle'})['id']

'feed_subtitle_46251501064;10157393058736065;;9'

### 一般貼文回饋資訊

In [9]:
i = pd.DataFrame(data['jsmods']['pre_display_requires'])[3][20]
i[1]['__bbox'].keys()

dict_keys(['complete', 'result', 'sequence_number', 'variables', 'incremental_chunks', 'extra_context'])

In [10]:
feedback_df = []
for i in pd.DataFrame(data['jsmods']['pre_display_requires'])[3]:
    try:
        feedback = i[1]['__bbox']['result']['data']['feedback']
        variables = i[1]['__bbox']['variables']
        ndf2 = pd.DataFrame(
            data=[{'PAGEID':feedback['owning_profile']['id'],
                   'COMMENT_COUNT':feedback['comment_count']['total_count'],
                   'DISPLAY_COMMENTS':feedback['display_comments']['count'],
                   'SHARE_COUNT':feedback['share_count']['count'],
                   'FEEDBACK':feedback['top_reactions'],
                   'FEEDBACKTARGETID':variables['feedbackTargetID'],
                   'storyID':variables['storyID']}],
            columns=['PAGEID', 'storyID', 'COMMENT_COUNT', 'DISPLAY_COMMENTS', 'SHARE_COUNT', 'FEEDBACK', 'FEEDBACKTARGETID'])
        feedback_df.append(ndf2)
    except:
        pass
pd.concat(feedback_df, ignore_index=True)

PAGEID                            storyID  COMMENT_COUNT  \
0   46251501064  S:_I46251501064:10157388139321065           1971   
1   46251501064  S:_I46251501064:10157392692396065           5701   
2   46251501064  S:_I46251501064:10157392630056065            768   
3   46251501064  S:_I46251501064:10157389825521065           1365   
4   46251501064  S:_I46251501064:10157387730691065           2182   
5   46251501064  S:_I46251501064:10157382322931065           1633   
6   46251501064  S:_I46251501064:10157381306496065           9909   
7   46251501064  S:_I46251501064:10157379370406065           2190   
8   46251501064  S:_I46251501064:10157391422461065           2735   
9   46251501064  S:_I46251501064:10157380975071065           2440   
10  46251501064  S:_I46251501064:10157382683276065           1675   
11  46251501064  S:_I46251501064:10157386531836065           1766   
12  46251501064  S:_I46251501064:10157389204006065           3090   
13  46251501064  S:_I46251501064:10157383311666065           3146   
14  46251501064  S:_I46251501064:10157391142726065           3001   
15  46251501064  S:_I46251501064:10157393058736065           5635   
16  46251501064  S:_I46251501064:10157387820716065            661   

    DISPLAY_COMMENTS  SHARE_COUNT  \
0                979          961   
1               3768         1319   
2                467          327   
3                764          825   
4               1212          918   
5                908         1185   
6               3768         3157   
7                982          759   
8               1695         1712   
9               1141         1405   
10               946          702   
11               867          794   
12              2046         1469   
13              1451         1104   
14              1884         1943   
15              3601         1467   
16               345          257   

                                             FEEDBACK  \
0   {'edges': [{'reaction_count': 65560, 'node': {...   
1   {'edges': [{'reaction_count': 75794, 'node': {...   
2   {'edges': [{'reaction_count': 23809, 'node': {...   
3   {'edges': [{'reaction_count': 35872, 'node': {...   
4   {'edges': [{'reaction_count': 92588, 'node': {...   
5   {'edges': [{'reaction_count': 58599, 'node': {...   
6   {'edges': [{'reaction_count': 91651, 'node': {...   
7   {'edges': [{'reaction_count': 39661, 'node': {...   
8   {'edges': [{'reaction_count': 85050, 'node': {...   
9   {'edges': [{'reaction_count': 55141, 'node': {...   
10  {'edges': [{'reaction_count': 35832, 'node': {...   
11  {'edges': [{'reaction_count': 42829, 'node': {...   
12  {'edges': [{'reaction_count': 77631, 'node': {...   
13  {'edges': [{'reaction_count': 86619, 'node': {...   
14  {'edges': [{'reaction_count': 56523, 'node': {...   
15  {'edges': [{'reaction_count': 72635, 'node': {...   
16  {'edges': [{'reaction_count': 22106, 'node': {...   

                        FEEDBACKTARGETID  
0   ZmVlZGJhY2s6MTAxNTczODgxMzkzMjEwNjU=  
1   ZmVlZGJhY2s6MTAxNTczOTI2OTIzOTYwNjU=  
2   ZmVlZGJhY2s6MTAxNTczOTI2MzAwNTYwNjU=  
3   ZmVlZGJhY2s6MTAxNTczODk4MjU1MjEwNjU=  
4   ZmVlZGJhY2s6MTAxNTczODc3MzA2OTEwNjU=  
5   ZmVlZGJhY2s6MTAxNTczODIzMjI5MzEwNjU=  
6   ZmVlZGJhY2s6MTAxNTczODEzMDY0OTYwNjU=  
7   ZmVlZGJhY2s6MTAxNTczNzkzNzA0MDYwNjU=  
8   ZmVlZGJhY2s6MTAxNTczOTE0MjI0NjEwNjU=  
9   ZmVlZGJhY2s6MTAxNTczODA5NzUwNzEwNjU=  
10  ZmVlZGJhY2s6MTAxNTczODI2ODMyNzYwNjU=  
11  ZmVlZGJhY2s6MTAxNTczODY1MzE4MzYwNjU=  
12  ZmVlZGJhY2s6MTAxNTczODkyMDQwMDYwNjU=  
13  ZmVlZGJhY2s6MTAxNTczODMzMTE2NjYwNjU=  
14  ZmVlZGJhY2s6MTAxNTczOTExNDI3MjYwNjU=  
15  ZmVlZGJhY2s6MTAxNTczOTMwNTg3MzYwNjU=  
16  ZmVlZGJhY2s6MTAxNTczODc4MjA3MTYwNjU=

In [ ]:
# reaction = pd.DataFrame(feedback['top_reactions']['edges'])
# reaction['reaction_type'] = reaction['node'].apply(lambda x: x['reaction_type'])
# pd.DataFrame(data = reaction['reaction_count']).c#['node'][0]['reaction_type']
# #['node'][0]['reaction_type']
# # for react in reaction['node']:
# #     reaction[reaction_type] = react['reaction_type']
# # reaction

In [ ]:
reaction['node'][0]

### 直播類貼文

In [11]:
for i in pd.DataFrame(data['jsmods']['require'])[3]:
    if 'feedbacktarget' in str(i):
        ndata = i
        break
ndata[2]

{'comments': [{'body': {'text': '謝謝總統～讓台灣安全❤️',
    'ranges': [],
    'aggregatedranges': [],
    'textdelightranges': []},
   'isfeatured': True,
   'likecount': 109,
   'hasviewerliked': False,
   'canremove': False,
   'canreport': False,
   'canedit': False,
   'canmutemembers': False,
   'isauthorbot': False,
   'isauthorweakreference': False,
   'isauthororiginalposter': False,
   'isauthornoncoworker': False,
   'istranslatable': False,
   'candeleteandblockcommenter': False,
   'canviewerremovecommenter': False,
   'canseeremovecontentoptions': False,
   'candeletecommentwithfeedback': False,
   'viewercanlike': False,
   'cancomment': False,
   'spamreplycount': 0,
   'recentreplytimestamp': {'time': 1617326194,
    'text': '4月1日下午6:16',
    'verbose': '2021年4月1日 星期四下午6:16'},
   'canembed': False,
   'canEditConstituentTitle': False,
   'hasConstituentBadge': False,
   'hasFriendsOnlyBadge': False,
   'videoTimeOffset': 168,
   'postedLiveState': 'Live',
   'needsApproval': Fa

In [12]:
for i in pd.DataFrame(data['jsmods']['pre_display_requires'])[3]:
    if '__bbox' in str(i):
        feedback = i[1]['__bbox']['result']['data']['feedback']
        break

In [13]:
reactions = pd.DataFrame(feedback['top_reactions']['edges'])
reactions['reaction_type'] = reactions['node'].apply(lambda x: x['reaction_type'])
pd.pivot_table(reactions, values= 'reaction_count',columns='reaction_type')

reaction_type   ANGER  HAHA   LIKE  LOVE  SORRY  SUPPORT  WOW
reaction_count     31    45  65560  1015      6      557   16

In [14]:
def CrawlPosts(PageUrl, date='2019-03-15'):
    print(PageUrl)
    PageID = get_pageid(PageUrl) 

    # 基本參數
    timeline_cursor = ''
    max_date =  datetime.datetime.now()
    break_times = 0
    content_df = [] # 貼文內容
    feedback_df = [] # 心情內容
    while max_date >= datetime.datetime.strptime(date, '%Y-%m-%d') and break_times <=10:
        try:
            url = 'https://www.facebook.com/pages_reaction_units/more/'
            params = {'page_id': PageID,
                      'cursor': str({"timeline_cursor":timeline_cursor,
                                     "timeline_section_cursor":'{}',
                                     "has_next_page":'true'}), 
                      'surface': 'www_pages_home',
                      'unit_count': 20,
                      '__a': '1'}
            resp = requests.get(url, params=params)
            data = json.loads(re.sub(r'for \(;;\);','',resp.text))

            # 貼文內容：貼文姓名、貼文人ID、貼文ID、時間、內容
            soup = BeautifulSoup(data['domops'][0][3]['__html'])
            for i in soup.findAll('div', {'class':'userContentWrapper'}):
                # 因為會有鎖文的情況，當有鎖文的情況時就會無法讀取貼文內容
                # 有些是置入的廣告不會有時間，需要另外處理
                # 有些是置入的廣告沒有page_id 遇到直接剔除~
                try:
                    ndf1 = pd.DataFrame(data=[{'NAME':i.find('img')['aria-label'],
                                           'TIME': datetime.datetime.fromtimestamp(int(i.find('abbr')['data-utime'])),
                                           'CONTENT': i.find('div',{'data-testid':'post_message'}).text,
                                           'PAGEID':re.findall('[0-9]{5,}', i.find('div',{'data-testid':'story-subtitle'})['id'])[0],
                                           'POSTID':re.findall('[0-9]{5,}', i.find('div',{'data-testid':'story-subtitle'})['id'])[1]}],
                                   columns=['NAME', 'PAGEID', 'POSTID', 'TIME', 'CONTENT'])
                    content_df.append(ndf1)
                except:
                    pass 
                
            # 一般貼文回饋資訊：
            for i in pd.DataFrame(data['jsmods']['pre_display_requires'])[3]:
                try:
                    feedback = i[1]['__bbox']['result']['data']['feedback']
                    variables = i[1]['__bbox']['variables']
                    top_reactions = feedback['top_reactions']
                    ndf2 = pd.DataFrame(data=[{'PAGEID':feedback['owning_profile']['id'],
                                               'COMMENT_COUNT':feedback['comment_count']['total_count'],
                                               'DISPLAY_COMMENTS':feedback['display_comments']['count'],
                                               'SHARE_COUNT':feedback['share_count']['count'],
#                                                'FEEDBACKTARGETID':variables['feedbackTargetID'],
                                               'POSTID':variables['storyID'].split(':', -1)[-1]}],
                                        columns=['PAGEID', 'POSTID', 'COMMENT_COUNT', 'DISPLAY_COMMENTS', 'SHARE_COUNT']) # 'FEEDBACKTARGETID'
                    react = pd.DataFrame(top_reactions['edges'])
                    react['reaction_type'] = react['node'].apply(lambda x: x['reaction_type'])
                    react = pd.DataFrame(data = {'reaction_type':react['reaction_type'],
                                                 'reaction_count':react['reaction_count']}).set_index(keys='reaction_type').T.reset_index(drop=True)
                    ndf2 = pd.concat([ndf2, react], axis=1)
                    feedback_df.append(ndf2)
                except:
                    pass
            pd.concat(feedback_df, ignore_index=True)
                    
            # 直播貼文回饋資訊
            for i in pd.DataFrame(data['jsmods']['require'])[3]:
                try:
                    ndf3 = pd.DataFrame(data= [{'PAGEID':i[2]['feedbacktarget']['actorid'],
                                                'COMMENT_COUNT':i[2]['feedbacktarget']['commentcount'],
                                                'DISPLAY_COMMENTS':i[2]['feedbacktarget']['commentcount'],
                                                'SHARE_COUNT':i[2]['feedbacktarget']['sharecount'],
#                                                 'FEEDBACKTARGETID':i[2]['feedbacktarget']['targetfbid'],
                                                'POSTID':i[2]['feedbacktarget']['targetfbid'],
                                                'LIKE':i[2]['feedbacktarget']['likecount']}],
                                       columns=['PAGEID', 'POSTID', 'COMMENT_COUNT', 'DISPLAY_COMMENTS', 'SHARE_COUNT','LIKE']) # 'FEEDBACKTARGETID'
                    feedback_df.append(ndf3)
                except:
                    pass
                    
            # 更新資訊
            max_date = ndf1['TIME'].max()
            print('TimeStamp: {}.'.format(ndf1['TIME'].max()))
            
            # 最後一則留言的編號
            timeline_cursor = re.findall(r'timeline_cursor\\u002522\\u00253A\\u002522(.*?)\\u002522\\u00252C\\u002522timeline_section_cursor',resp.text)[0]
            # 歸零錯誤次數
            break_times = 0
        except:
            break_times += 1
            time.sleep(0.5)
            print('break_times:', break_times)
            
    # 整併貼文內容與回饋資訊
    content_df = pd.concat(content_df, ignore_index=True)
    feedback_df = pd.concat(feedback_df, ignore_index=True, sort=False)
    df = pd.merge(left=content_df, right=feedback_df, how='left', on=['PAGEID', 'POSTID'])
    df['UPDATETIME'] = datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S")      
    print('There are {} posts in DataFrame.'.format(str(df.shape[0])))
    return df

In [15]:
PageUrl='https://www.facebook.com/tstartel/'
PageUrl='https://www.facebook.com/tsaiingwen'
# PageUrl = 'https://www.facebook.com/polin66666'
df = CrawlPosts(PageUrl=PageUrl, date='2021-04-01')

https://www.facebook.com/tsaiingwen
TimeStamp: 2021-03-25 18:12:34.
There are 18 posts in DataFrame.


In [16]:
df

NAME       PAGEID             POSTID                TIME  \
0   蔡英文 Tsai Ing-wen  46251501064  10157393058736065 2021-04-02 18:01:46   
1   蔡英文 Tsai Ing-wen  46251501064  10157392692396065 2021-04-02 11:18:48   
2   蔡英文 Tsai Ing-wen  46251501064  10157392630056065 2021-04-02 10:08:12   
3   蔡英文 Tsai Ing-wen  46251501064  10157391422461065 2021-04-01 18:27:57   
4   蔡英文 Tsai Ing-wen  46251501064  10157391142726065 2021-04-01 12:31:45   
5   蔡英文 Tsai Ing-wen  46251501064  10157389825521065 2021-03-31 18:54:10   
6   蔡英文 Tsai Ing-wen  46251501064  10157389204006065 2021-03-31 09:07:13   
7   蔡英文 Tsai Ing-wen  46251501064  10157388139321065 2021-03-30 19:10:44   
8   蔡英文 Tsai Ing-wen  46251501064   1144375719343634 2021-03-30 15:56:30   
9   蔡英文 Tsai Ing-wen  46251501064  10157387820716065 2021-03-30 12:30:08   
10  蔡英文 Tsai Ing-wen  46251501064  10157387730691065 2021-03-30 11:19:46   
11  蔡英文 Tsai Ing-wen  46251501064  10157386531836065 2021-03-29 17:49:09   
12  蔡英文 Tsai Ing-wen  46251501064  10157383311666065 2021-03-27 23:09:20   
13  蔡英文 Tsai Ing-wen  46251501064  10157382683276065 2021-03-27 14:17:50   
14  蔡英文 Tsai Ing-wen  46251501064  10157382322931065 2021-03-27 08:45:15   
15  蔡英文 Tsai Ing-wen  46251501064  10157381306496065 2021-03-26 20:26:28   
16  蔡英文 Tsai Ing-wen  46251501064  10157380975071065 2021-03-26 14:26:08   
17  蔡英文 Tsai Ing-wen  46251501064  10157379370406065 2021-03-25 18:12:34   

                                              CONTENT  COMMENT_COUNT  \
0   非常遺憾，在連假第一天就發生事故，造成重大傷亡，我和國人同感哀傷。 　　 今天上午我接獲通報...           5635   
1   今天早上，台鐵太魯閣號408車次列車，在花蓮大清水隧道發生出軌事故，目前搶救正在進行中。 　...           5701   
2   早安，四天連續假期開始了，你有安排返鄉或出門走走的行程嗎？ 　　 需要開車的朋友，可以參考這...            768   
3   台鐵 #最美區間車 開箱！ 　　 今天，台鐵的EMU900型電聯車，從「台灣頭」基隆展開首航...           2735   
4   中國時報說我不重視社工、不重視加薪，這是斷章取義的說法。 　　 我想花一點時間，說明政府的努...           3001   
5   謝謝社工夥伴的付出，我們一起挺社工！ 　　 這幾年來，我們推動長照2.0，保護兒少、婦女、身...           1365   
6   水庫加倍清淤中，這些怪手也很辛苦！ 　　 面對56年來最嚴峻的水情，我們除了開設 #旱災中央...           3090   
7   熱烈歡迎帛琉總統來訪，台灣、帛琉、美國三方強化合作！ 　　 帛琉的惠恕仁總統（Preside...           1971   
8                大家午安！我正在總統府內會見帛琉總統惠恕仁率領的訪團，歡迎大家收看直播。           2601   
9   大家午安！今天下午四點，我將在總統府內，會見帛琉總統惠恕仁（ President Suran...            661   
10  清明節快到了，來史明歐吉桑的墓園看看他。 　　 我想告訴歐吉桑，台灣依然是自由民主的台灣。我...           2182   
11  台帛旅遊泡泡開放，帛琉觀光四大亮點一次告訴你！ 　　 帛琉總統惠恕仁（President S...           1766   
12  時隔兩年，大港的船鳴聲，再度響起！ 　　 港邊是鬥陣的所在，也是咱的所在。人生的音樂祭 Me...           3146   
13  從歷史的縫隙中，找出真相，還給當事人一個公道，這就是轉型正義的意義。 　　 今天 促進轉型正...           1675   
14  出門掃墓，請小心留意，避免火燒山！ 　　 清明節快到了，很多人提前分流掃墓，但這陣子也傳出森...           1633   
15  這幾天，維吾爾族人權以及新疆棉花的議題，再度因為中國民間抵制跨國公司的情緒，受到國際的關注。...           9909   
16  台美 #設立海巡工作小組瞭解備忘錄 完成簽署！ 　　 美東時間昨天早上，駐美代表 蕭美琴 B...           2440   
17  集中營的歷史，我們不能遺忘。 　　 每年，駐台北以色列經濟文化辦事處 Israel in T...           2190   

    DISPLAY_COMMENTS  SHARE_COUNT   LIKE  SUPPORT    SORRY     WOW    LOVE  \
0               3601         1467  72635  17334.0  23478.0   216.0   878.0   
1               3768         1319  75794  21187.0  16853.0  1019.0   673.0   
2                467          327  23809    235.0     14.0    15.0   271.0   
3               1695         1712  85050    495.0     34.0   199.0  1221.0   
4               1884         1943  56523    861.0     24.0    57.0   771.0   
5                764          825  35872    470.0      7.0    10.0   516.0   
6               2046         1469  77631   1853.0     14.0    35.0   914.0   
7                979          961  65560    557.0      6.0    16.0  1015.0   
8               2601          647  15766      NaN      NaN     NaN     NaN   
9                345          257  22106    241.0      NaN     8.0   315.0   
10              1212          918  92588   1097.0     91.0    21.0  2398.0   
11               867          794  42829    292.0      4.0    38.0   703.0   
12              1451         1104  86619    410.0      6.0    28.0  1312.0   
13               946          702  35832    528.0     17.0    13.0   375.0   
14               908         118

In [15]:
df.head(100).to_excel('sample_post.xlsx')

## 留言
以下兩種方式都可以抓客戶的留言，但抓回來的資訊不一樣


### 一般貼文使用參數

In [8]:
# df = []
# # 設置基本參數
# url = 'https://www.facebook.com/api/graphql/'
# # feedbackTargetID='ZmVlZGJhY2s6MjY0MjIzNTI0MjY4MDI5MA==	' # 2642235242680290
# feedbackTargetID='2642313842672430' # 2642235242680290
# has_next_page = True
# break_times = 0
# doc_id = '3774913485867119'
# end_cursor=''
# payload = {'variables':str({"after":end_cursor,
#                             "feedbackID":feedbackTargetID,
#                             "first":10, # 1682
#                             "topLevelViewOption":"RANKED_UNFILTERED"}),
#            'doc_id':doc_id}
# resp = requests.post(url, data = payload)
# jd = resp.json()
# jd['data']['feedback']['display_comments']['page_info']


In [9]:
# for i in jd['data']['feedback']['display_comments']['edges']:
#     print('TYEPNAME: ', i['node']['__typename'])
#     print('AUTHOR: ', i['node']['author']['id'])
#     print('NAME: ', i['node']['author']['name'])
#     print('TEXT: ',i['node']['body']['text'])
#     print('COMMENT_ID: ',i['node']['can_comment']['id'])
#     print('TIME:', i['node']['created_time'])
#     print('display_comments', i['node']['feedback']['display_comments']['count'])
#     print('reactors:', i['node']['feedback']['reactors']['count'])
#     # print('legacy_token: ', i['node']['legacy_token'])
#     print('POSTID: ', re.findall('[0-9]{1,}', i['node']['legacy_token'])[0])
#     print('SHARE_FBID: ', re.findall('[0-9]{1,}', i['node']['legacy_token'])[1])
#     print('='*88)

In [10]:
# # 一般貼文
# def Get_Comments(FEEDBACKTARGETID):
#     df = []
#     break_times = 0
#     # 送出爬蟲請求
#     url = 'https://www.facebook.com/api/graphql/'
#     doc_id = '3774913485867119'
#     end_cursor=''
#     while break_times<=20: 
#         try:
#             payload = {'variables':str({"after":end_cursor,
#                                         "feedbackID":FEEDBACKTARGETID,
#                                         "first":50, # 1682
#                                         # "topLevelViewOption":"RANKED_UNFILTERED"
#                                         }),
#                        'doc_id':doc_id}
#             resp = requests.post(url, data = payload)
#             # 解析回傳資料
#             data = resp.json()['data']
#             for i in data['feedback']['display_comments']['edges']:
#                 try:
#                     TEXT = i['node']['body']['text']
#                 except:
#                     TEXT = ''
#                 ndf = pd.DataFrame(data = [{'TIME':(datetime.datetime.fromtimestamp(int(i['node']['created_time'])) + datetime.timedelta(hours=8)).strftime("%Y-%m-%d %H:%M"),
#                                             'TYPENAME':i['node']['__typename'],
#                                             'AUTHOR':i['node']['author']['id'],
#                                             'NAME':i['node']['author']['name'],
#                                             'COMMENTID':i['node']['can_comment']['id'],
#                                             'DISPLAY_COMMENTS': i['node']['feedback']['display_comments']['count'],
#                                             'REACTORS':i['node']['feedback']['reactors']['count'],
#                                             'FEEDBACKTARGETID':FEEDBACKTARGETID,
#                                             'TEXT':TEXT,
#                                             'POSTID': re.findall('[0-9]{1,}', i['node']['legacy_token'])[0],
#                                             'SHARE_FBID': re.findall('[0-9]{1,}', i['node']['legacy_token'])[1],
#                                             'UPDATETIME':(datetime.datetime.now() + datetime.timedelta(hours=8)).strftime("%Y-%m-%d %H:%M")}],
#                                    columns=['NAME', 'AUTHOR', 'TIME', 'TEXT','TYPENAME', 'DISPLAY_COMMENTS', 'FEEDBACKTARGETID', 'REACTORS','COMMENTID','POSTID', 'SHARE_FBID','UPDATETIME'])
#                 df.append(ndf)
#             # page_info：記錄這次爬蟲抓到最後一則留言的編號            
#             end_cursor = data['feedback']['display_comments']['page_info']['end_cursor']
#             break_times = 0
#         except:
#             time.sleep(1)
#             break_times += 1
        
#     # 完成後更新
#     df = pd.concat(df,ignore_index=True)
#     df = df.loc[:,['NAME', 'AUTHOR', 'TIME', 'TEXT', 'TYPENAME', 'DISPLAY_COMMENTS', 'FEEDBACKTARGETID', 'REACTORS', 'COMMENTID', 'POSTID', 'SHARE_FBID', 'UPDATETIME']]
#     print(df.shape)
#     return df

In [11]:
# df = Get_Comments('2749876898582790')
# df

### 直播類貼文使用參數
從0開始加50,直到沒有留言才停

In [3]:
def Get_Comments(PostID):
    df = []
    break_times = 0
    fail_cnt = 1
    offset=0
    url = 'https://www.facebook.com/ajax/ufi/comment_fetch.php'
    while fail_cnt <= 30:
        try:
            params = {'ft_ent_identifier': PostID,
                      'offset': offset,
                      'length': 50,
                      '__a': 1}
            resp = requests.get(url, params=params)
            data = json.loads(re.sub(r'for \(;;\);','',resp.text))
            id2name=pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['profiles']).loc[['name','gender'],:].T.reset_index()
            id2name.columns = ['AUTHOR', 'NAME','GENDER']
            replies = pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['commentlists']['replies']).loc['count',:].reset_index()
            replies['index'] = replies['index'].apply(lambda x: x.split('_', -1)[1])
            replies.columns = ['COMMENTID', 'REPLIES']

            df2 = []
            for i in pd.DataFrame(data['jsmods']['require'])[3][0][1]['comments']:
                ndf = pd.DataFrame(data = [{'TYPENAME':i['__typename'],
                                            'AUTHOR':i['author'],
                                            'TEXT':i['body']['text'],
                                            'POSTID': re.findall('[0-9]{1,}', i['id'])[0],
                                            'COMMENTID': re.findall('[0-9]{1,}', i['id'])[1],
                                            'PARENTCOMMENTAUTHORID': i['parentcommentauthorid'],
                                            'PARENTCOMMENTID': i['parentcommentid'],
                                            'LIKECOUNT': i['likecount'],
                                            'TIME':datetime.datetime.fromtimestamp(int(i['timestamp']['time'])).strftime("%Y-%m-%d %H:%M"),
                                            'UPDATETIME':datetime.datetime.now().strftime("%Y-%m-%d %H:%M")}],
                                   columns=['AUTHOR', 'TIME' ,'TEXT','TYPENAME','COMMENTID','PARENTCOMMENTAUTHORID', 'PARENTCOMMENTID', 'LIKECOUNT', 'POSTID', 'UPDATETIME'])
                df2.append(ndf)
            # 合併資料
            df2 = pd.concat(df2, ignore_index=True)
            df2 = pd.merge(df2, id2name,  how='left', on='AUTHOR')
            df2 = pd.merge(df2, replies,  how='left', on='COMMENTID')
            df.append(df2)
            break_times = 0
            fail_cnt = 0
            
        except:
            fail_cnt += 1

        offset += 50
    # 完成後更新
    df = pd.concat(df,ignore_index=True)
    df = df.loc[:,['NAME', 'AUTHOR', 'TIME', 'TEXT', 'REPLIES', 'LIKECOUNT', 'POSTID', 'COMMENTID', 'PARENTCOMMENTAUTHORID', 'PARENTCOMMENTID', 'GENDER', 'TYPENAME', 'UPDATETIME']]
    print(df.shape)
    return df

In [4]:
# %%time
df = Get_Comments('160361789041991')
df

(48, 13)


NAME           AUTHOR              TIME  \
0             林宜靜  100000253698209  2021-02-05 23:12   
1             許宜芬  100057902652308  2021-03-25 14:08   
2             許宜芬  100057902652308  2021-03-19 11:05   
3     Shu Ya Shen  100058161481107  2021-03-24 21:00   
4   Li Ming Chieh  100058097764014  2021-03-04 13:00   
5             黃香君  100058045473203  2021-03-25 14:04   
6             黃孟珊  100057595884761  2021-03-12 18:22   
7     Edward Zhou  100057924431425  2021-03-20 20:41   
8             陳玉萍  100058073282115  2021-03-10 17:02   
9             張文琳  100013245451830  2021-02-04 20:40   
10            王瑜庭  100057732859257  2021-03-23 14:07   
11            李任強  100002325016179  2021-04-12 22:44   
12    Shu Ya Shen  100057746688918  2021-02-27 15:03   
13       Vicky Li       1748149901  2021-02-21 15:07   
14            許郁欣  100057887412785  2021-03-12 18:14   
15     Adele Yang  100057737779142  2021-02-28 21:05   
16            羅豐賢  100064703630266  2021-03-22 13:24   
17            陳柏均  100058052855633  2021-03-19 11:09   
18            藍宇翔  100012708612664  2021-03-10 19:55   
19            郭慧貞  100057121645854  2021-03-22 13:27   
20            李維哲  100057944440609  2021-03-12 18:26   
21            謝曉芬  100057410294951  2021-03-19 10:46   
22             錢錢  100000549459530  2020-08-22 21:10   
23             玉婷       1043036553  2020-12-30 18:46   
24            林淑卿  100057398323845  2021-03-07 11:08   
25             蕭官  100000077793499  2020-12-15 08:02   
26             宣閔  100000409200562  2021-04-09 01:17   
27            林揚淳  100003796653727  2021-04-15 00:22   
28            李平道  100064712930153  2021-03-24 21:11   
29            陳僑僑  100006839477217  2021-04-10 14:02   
30            謝孟樺  100000695346659  2021-02-10 12:14   
31      Cathy Tam       1426348167  2021-02-21 22:23   
32            劉慧文  100000118775859  2021-01-16 06:48   
33     Siang Wang  100000219107318  2021-02-17 20:52   
34            余子涵  100000365361146  2021-04-11 08:33   
35       Leo Chen  100005806386143  2020-11-13 13:07   
36         花小町 ナナ  100009020259774  2021-02-15 23:46   
37            陳愷文  100003926852283  2020-08-13 09:45   
38            妮可菈  100000315931226  2021-01-25 23:58   
39            黃慧珍  100057379184679  2021-03-20 20:42   
40            余其杰  100000194561753  2021-01-21 15:11   
41            李政育  100004710300346  2021-04-16 08:08   
42            陳家瑩  100058102591080  2021-03-26 11:41   
43            王豪偉  100001831419642  2021-01-09 21:53   
44            郭賢賢  100000181890396  2021-04-08 15:33   
45      Emma Chen  100010462928713  2021-01-03 00:28   
46            蕭仁閔       1851148057  2020-08-30 13:18   
47            林貞吟  100001601398039  2020-11-17 22:33   

                                   TEXT REPLIES  LIKECOUNT           POSTID  \
0                        Huang Ting就是這個       0          1  160361789041991   
1                    有人可以分享心得嗎? 想了解是否好用       3          1  160361789041991   
2                   請問要怎麼看到影像? 要額外裝電池嗎?       2          0  160361789041991   
3                     請問要怎麼看到影像? 會不會很黑?       2          0  160361789041991   
4       畫面很清楚 比其他牌子好用\r價格又比誠品賣的便宜很多  推!       0          0  160361789041991   
5                        第一次挖耳朵可以看得很清楚!       0          1  160361789041991   
6                這價格很漂亮! 比誠品便宜多了 2隻還有優惠       0          0  160361789041991   
7               第一次挖耳朵可以看得很清楚 耳棒也很柔軟不會痛       0          1  160361789041991   
8                       用手機看著弄真的很方便 很好用       0          0  160361789041991   
9                           問一下那一個手機可以用       1          0  160361789041991   
10                   白色款很有質感 買給男友當生日禮物~       0          0  160361789041991   
11                          是問蘋果i8可以用嗎？       2          0  160361789041991   
12                    有人可以分享心得嗎? 想買給老公用       4          2  160361789041991   
13                  請問耳扒只有一個嗎？還是有可以替換的？       2          0  160361789041991   
14                          要用安卓還是蘋果手機?       1          0  160361789041991   
15  

In [5]:
df.head(100).to_excel('160361789041991.xlsx')

## 回覆
跟直播類貼文的抓法只有差在最一開始request/post的網址與送的參數

In [38]:
# url = 'https://www.facebook.com/ajax/ufi/reply_fetch.php'
# params = {'ft_ent_identifier': 2656004354628554,
#           'parent_comment_ids[0]': '2656004354628554_224760008892501',
#           'offsets[0]': 41,
#           'lengths[0]': 50,
#           '__a': 1,
#           }
# resp = requests.get(url, params=params)
# data = json.loads(re.sub(r'for \(;;\);','',resp.text))

In [39]:
# replies = pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['commentlists']['replies']).loc['count',:].reset_index()
# replies['index'] = replies['index'].apply(lambda x: x.split('_', -1)[1])
# replies.columns = ['COMMENTID', 'REPLIES']
# replies.head(5)

In [40]:
# id2name=pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['profiles']).loc[['name','gender'],:].T.reset_index()
# id2name.columns = ['AUTHOR', 'NAME','GENDER']
# id2name.head(5)

In [41]:
# for i in pd.DataFrame(data['jsmods']['require'])[3][0][1]['comments']:
#     try:
#         accessibilityLabel = i['attachment']['metadata']['accessibilityLabel']
#     except:
#         accessibilityLabel = ''
#     try:
#         type = i['attachment']['type']
#     except:
#         type = ''
#     print('ACCESSIBILITYLABEL:', accessibilityLabel)
#     print('TYPE:', type)
#     print('TYPENAME: ', i['__typename'])
#     print('AUTHOR: ', i['author'])
#     print('TEXT: ', i['body']['text'])
#     print('POSTID: ', re.findall('[0-9]{1,}', i['id'])[0])
#     print('COMMENTID: ', re.findall('[0-9]{1,}', i['id'])[1])
#     print('parentcommentauthorid: ', i['parentcommentauthorid'])
#     print('parentcommentid: ', i['parentcommentid'])
#     # print('SPAMREPLYCOUNT:', i['spamreplycount'])
#     print('LIKECOUNT: ', i['likecount'])
#     print('TIME: ', i['timestamp']['time'])
#     print('='*88)

In [42]:
# url = 'https://www.facebook.com/ajax/ufi/reply_fetch.php'
# params = {'ft_ent_identifier': 2656004354628554,
#           'parent_comment_ids[0]': '2656004354628554_224760008892501',
#           'offsets[0]': 0,
#           'lengths[0]': 50,
#           '__a': 1,
#           }
# resp = requests.get(url, params=params)
# data = json.loads(re.sub(r'for \(;;\);','',resp.text))
# id2name=pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['profiles']).loc[['name','gender'],:].T.reset_index()
# id2name.columns = ['AUTHOR', 'NAME','GENDER']
# replies = pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['commentlists']['replies']).loc['count',:].reset_index()
# replies['index'] = replies['index'].apply(lambda x: x.split('_', -1)[1])
# replies.columns = ['COMMENTID', 'REPLIES']
# df = []
# for i in pd.DataFrame(data['jsmods']['require'])[3][0][1]['comments']:
#     try:
#         accessibilityLabel = i['attachment']['metadata']['accessibilityLabel']
#     except:
#         accessibilityLabel = ''
#     try:
#         type = i['attachment']['type']
#     except:
#         type = ''
#     ndf = pd.DataFrame(data = [{'TYPENAME':i['__typename'],
#                                 'AUTHOR':i['author'],
#                                 'TYPE':type,
#                                 'TEXT':i['body']['text'],
#                                 'ACCESSIBILITYLABEL': accessibilityLabel,
#                                 'POSTID': re.findall('[0-9]{1,}', i['id'])[0],
#                                 'COMMENTID': re.findall('[0-9]{1,}', i['id'])[1],
#                                 'PARENTCOMMENTAUTHORID': i['parentcommentauthorid'],
#                                 'PARENTCOMMENTID': i['parentcommentid'],
#                                 'LIKECOUNT': i['likecount'],
#                                 'TIME':datetime.datetime.fromtimestamp(int(i['timestamp']['time'])).strftime("%Y-%m-%d %H:%M"),
#                                 'UPDATETIME':datetime.datetime.now().strftime("%Y-%m-%d %H:%M")}],
#                        columns=['AUTHOR', 'TIME','TYPE' ,'TEXT','ACCESSIBILITYLABEL','TYPENAME','COMMENTID', 'PARENTCOMMENTAUTHORID', 'PARENTCOMMENTID', 'LIKECOUNT', 'POSTID', 'UPDATETIME'])
#     df.append(ndf)
# df=pd.concat(df, ignore_index=True)
# df = pd.merge(id2name,df,  how='left', on='AUTHOR')
# df = pd.merge(df, replies,  how='left', on='COMMENTID')
# df

In [19]:
def Get_Replies(POSTID, COMMENTID):
    df = []
    break_times = 0
    cnt = 1
    offset=0
    url = 'https://www.facebook.com/ajax/ufi/reply_fetch.php'
    while cnt >=1:
        try:
            params = {'ft_ent_identifier': POSTID,
                      'parent_comment_ids[0]': POSTID + '_' + COMMENTID,
                      'offsets[0]': offset,
                      'lengths[0]': 50,
                      '__a': 1}
            resp = requests.get(url, params=params)
            data = json.loads(re.sub(r'for \(;;\);','',resp.text))
            id2name=pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['profiles']).loc[['name','gender'],:].T.reset_index()
            id2name.columns = ['AUTHOR', 'NAME','GENDER']
            replies = pd.DataFrame(pd.DataFrame(data['jsmods']['require'])[3][0][1]['commentlists']['replies']).loc['count',:].reset_index()
            replies['index'] = replies['index'].apply(lambda x: x.split('_', -1)[1])
            replies.columns = ['COMMENTID', 'REPLIES']
         
            df2 = []
            for i in pd.DataFrame(data['jsmods']['require'])[3][0][1]['comments']:
                try:
                    accessibilityLabel = i['attachment']['metadata']['accessibilityLabel']
                except:
                    accessibilityLabel = ''
                try:
                    type = i['attachment']['type']
                except:
                    type = ''
                ndf = pd.DataFrame(data = [{'TYPENAME':i['__typename'],
                                            'AUTHOR':i['author'],
                                            'TYPE':type,
                                            'TEXT':i['body']['text'],
                                            'ACCESSIBILITYLABEL': accessibilityLabel,
                                            'POSTID': re.findall('[0-9]{1,}', i['id'])[0],
                                            'COMMENTID': re.findall('[0-9]{1,}', i['id'])[1],
                                            'PARENTCOMMENTAUTHORID': i['parentcommentauthorid'],
                                            'PARENTCOMMENTID': i['parentcommentid'],
                                            'LIKECOUNT': i['likecount'],
                                            'TIME':datetime.datetime.fromtimestamp(int(i['timestamp']['time'])).strftime("%Y-%m-%d %H:%M"),
                                            'UPDATETIME':datetime.datetime.now().strftime("%Y-%m-%d %H:%M")}],
                                   columns=['AUTHOR', 'TIME','TYPE' ,'TEXT','ACCESSIBILITYLABEL','TYPENAME','COMMENTID', 'PARENTCOMMENTAUTHORID', 'PARENTCOMMENTID', 'LIKECOUNT', 'POSTID', 'UPDATETIME'])
                df2.append(ndf)
            # 合併資料
            df2 = pd.concat(df2, ignore_index=True)
            df2 = pd.merge(df2, id2name,  how='left', on='AUTHOR')
            df2 = pd.merge(df2, replies,  how='left', on='COMMENTID')
            df.append(df2)
            break_times = 0
            # 更新參數
            if df2.shape[0] >=1:
                cnt = df2.shape[0]
                offset += 50
        except:
            break
        
    # 完成後更新
    df = pd.concat(df,ignore_index=True)
    df = df.loc[:,['NAME', 'AUTHOR', 'TIME', 'TYPE', 'ACCESSIBILITYLABEL', 'TEXT', 'REPLIES', 'LIKECOUNT', 'POSTID', 'COMMENTID', 'PARENTCOMMENTAUTHORID', 'PARENTCOMMENTID','GENDER', 'TYPENAME', 'UPDATETIME']]
    print(df.shape)
    return df

In [21]:
df = Get_Replies(POSTID='10157156027271065', COMMENTID='10157156032961065')
df

(36, 15)


NAME           AUTHOR              TIME     TYPE  \
0                     張坤宏  100010081608297  2020-12-03 17:35            
1                     簡玅旼  100006405484930  2020-12-03 17:39            
2                     黃豐榮  100005922154701  2020-12-03 17:42            
3                Poco Lee  100008031423962  2020-12-03 18:27            
4   Chan Kuo-min Joe Chan  100000299983301  2020-12-03 18:09            
5                     梁家榮  100000489553899  2020-12-03 18:11            
6                      鄭尹  100007470466209  2020-12-03 18:31            
7               Elsa Yang  100028220670574  2020-12-03 18:31            
8               Elsa Yang  100028220670574  2020-12-03 18:35            
9                     黃奕程  100019199893884  2020-12-03 19:00            
10               Poco Lee  100008031423962  2020-12-03 19:04            
11              Elsa Yang  100028220670574  2020-12-03 19:32            
12                    呂玉彥  100028324085078  2020-12-03 19:42            
13                    吳細真  100022178144909  2020-12-03 19:43            
14                    王元姬  100001223689034  2020-12-03 19:55            
15                    陳昆雄  100000579335157  2020-12-03 20:59            
16                    蘇文良  100001179980536  2020-12-03 21:24            
17            Jackie Wang  100049591359321  2020-12-03 21:31            
18                    黃奕程  100019199893884  2020-12-03 21:39            
19                    李万宝  100023537654246  2020-12-03 21:40            
20                    林心放  100021240262045  2020-12-03 21:46    share   
21                    沈德垣  100012301337790  2020-12-03 21:57            
22                    謝鈞閎  100001121785196  2020-12-03 22:16            
23                    劉霓蔻  100004073572697  2020-12-04 00:41            
24      Wendy Christopher  100007108712631  2020-12-04 06:25            
25                    紀亭宇  100004021428335  2020-12-04 09:17            
26                     郑杰  100016468750954  2020-12-04 09:59            
27                    振华陈  100058583482091  2020-12-04 12:48            
28            Tsu Ik-tiân       1675041941  2020-12-04 16:23  sticker   
29                    紀建振  100002091658881  2020-12-04 19:05            
30              Akai Chen  100028108999105  2020-12-04 20:10            
31              Coca Mark  100022809317801  2020-12-05 02:24            
32                     刘振  100028504506076  2020-12-05 02:58            
33                    徐世樺  100000246940363  2020-12-05 07:44            
34            Eason Chien        688572676  2020-12-05 08:12            
35                    鄭文平  100001869529197  2020-12-06 17:35            

   ACCESSIBILITYLABEL                                               TEXT  \
0                                                   鄭宏輝 如果有，也應該的因為防疫比較重要   
1                                                     鄭宏輝 去錢櫃唱歌也要戴口罩？怎麼唱   
2                                                       張坤宏 去時戴著，開唱就不用吧！   
3                                           防疫優等生，變放牛班，下周英國開始施打新冠疫苗，台灣呢？   
4                                                   Poco Lee 下周英國全面施打???   
5                                                         不要去唱不就好了......   
6                                                   鄭宏輝 你回文比工作還勤奮實在難能可貴。   
7                                                       Poco Lee 要移民英國嗎🤔   
8                      請國人落實做好防疫臺灣能在疫情嚴峻的情況下生活沒受太大的影響就是國人配合政府的防疫☺也希望遏...   
9                                                          守住自己荷包，天佑台湾！🙏   
10                                                         Elsa Yang 無能？   
11                                 Poco Lee 對臺灣如此不滿何不找你滿意的地方居住🤔搬回你的祖國不敢🤔   
12                                                       Poco Lee 你還在崩潰啊   
13                                     Zhang Junk 嚼舌根的紅粉，滾回你的老家，別在台灣般弄是非   
14                                                              子彈防疫哦，北七   
15                                     Zhang Junk 要不要像你們中共軍直接開坦克直接壓百姓哪!?   
16                     鄭宏輝 

In [22]:
df.to_excel('sample_replies.xlsx')

# 爬蟲實作

## 抓取貼文

In [22]:
%%time
pages = ['https://www.facebook.com/ETtoday',
         'https://www.facebook.com/ETtodaySTAR',
         'https://www.facebook.com/crazyck101',
         'https://www.facebook.com/appledaily.tw',
         'https://www.facebook.com/news.ebc']

df = []
for page in pages:
    ndf = CrawlPosts(PageUrl = page, date='2019-01-01')
    df.append(ndf)
df = pd.concat(df, ignore_index=True)
print(df.shape)
df.head(3)

https://www.facebook.com/ETtoday
TimeStamp: 2020-06-13 14:00:11.
TimeStamp: 2020-06-13 11:53:53.
TimeStamp: 2020-06-13 09:30:03.
TimeStamp: 2020-06-13 06:10:57.
TimeStamp: 2020-06-13 01:40:35.
TimeStamp: 2020-06-12 22:12:33.
TimeStamp: 2020-06-12 19:30:18.
TimeStamp: 2020-06-12 16:58:00.
TimeStamp: 2020-06-12 14:40:08.
TimeStamp: 2020-06-12 12:07:27.
TimeStamp: 2020-06-12 09:37:01.
TimeStamp: 2020-06-12 06:30:22.
TimeStamp: 2020-06-12 00:48:19.
TimeStamp: 2020-06-11 21:12:41.
TimeStamp: 2020-06-11 18:09:44.
TimeStamp: 2020-06-11 16:00:29.
TimeStamp: 2020-06-11 13:36:03.
TimeStamp: 2020-06-11 10:24:22.
TimeStamp: 2020-06-11 07:50:17.
TimeStamp: 2020-06-11 04:00:13.
TimeStamp: 2020-06-10 23:00:45.
TimeStamp: 2020-06-10 19:36:19.
TimeStamp: 2020-06-10 17:07:15.
TimeStamp: 2020-06-10 15:05:09.
TimeStamp: 2020-06-10 13:00:22.
TimeStamp: 2020-06-09 15:03:32.
TimeStamp: 2020-06-08 15:36:21.
TimeStamp: 2020-06-07 18:18:00.
TimeStamp: 2020-06-06 22:29:27.
TimeStamp: 2020-06-06 03:40:49.
TimeSta

TimeStamp: 2020-03-25 16:45:58.
TimeStamp: 2020-03-24 20:15:00.
TimeStamp: 2020-03-24 08:20:06.
TimeStamp: 2020-03-23 17:22:50.
TimeStamp: 2020-03-22 11:25:38.
TimeStamp: 2020-03-21 07:25:00.
TimeStamp: 2020-03-20 09:10:20.
TimeStamp: 2020-03-19 14:35:57.
TimeStamp: 2020-03-18 19:20:00.
TimeStamp: 2020-03-18 01:50:40.
TimeStamp: 2020-03-17 08:40:23.
TimeStamp: 2020-03-16 17:20:47.
TimeStamp: 2020-03-15 16:18:08.
TimeStamp: 2020-03-14 18:50:39.
TimeStamp: 2019-12-31 17:50:57.
TimeStamp: 2019-12-29 20:10:00.
TimeStamp: 2019-12-27 22:55:00.
TimeStamp: 2019-12-26 01:10:00.
TimeStamp: 2019-12-24 06:00:05.
TimeStamp: 2019-12-22 14:30:55.
TimeStamp: 2019-12-20 18:34:21.
TimeStamp: 2019-09-29 07:30:01.
TimeStamp: 2019-09-26 21:50:00.
TimeStamp: 2019-09-24 21:30:01.
TimeStamp: 2019-09-23 01:40:00.
TimeStamp: 2019-09-20 21:20:13.
TimeStamp: 2019-09-19 19:10:02.
TimeStamp: 2019-09-18 14:46:00.
TimeStamp: 2019-09-16 17:00:01.
TimeStamp: 2019-06-27 09:50:00.
TimeStamp: 2019-06-25 09:15:02.
TimeStam

NAME           PAGEID            POSTID                TIME  \
0  ETtoday新聞雲  242305665805605  3472814259421380 2020-06-13 16:06:22   
1  ETtoday新聞雲  242305665805605  3472941216075351 2020-06-13 16:00:57   
2  ETtoday新聞雲  242305665805605  3472888116080661 2020-06-13 15:48:20   

                                             CONTENT  COMMENT_COUNT  \
0  研擬開放旅客轉機，但不過夜！（#妮塔）  👉快加入新聞雲LINE，即時新聞推播底家：http...            9.0   
1  阿公一踏出門就放下大石頭了！（#妮塔）  👉快加入新聞雲LINE，即時新聞推播底家：http...            7.0   
2  原來安佐是靠手搖飲收服獄友啊～(#妮塔）  👉快加入新聞雲LINE，即時新聞推播底家：htt...           42.0   

   DISPLAY_COMMENTS  SHARE_COUNT                      FEEDBACKTARGETID   LIKE  \
0               9.0          0.0  ZmVlZGJhY2s6MzQ3MjgxNDI1OTQyMTM4MA==   91.0   
1               6.0          0.0  ZmVlZGJhY2s6MzQ3Mjk0MTIxNjA3NTM1MQ==  252.0   
2              35.0          1.0  ZmVlZGJhY2s6MzQ3Mjg4ODExNjA4MDY2MQ==  212.0   

   HAHA  SORRY   WOW  ANGER  SUPPORT  LOVE           UPDATETIME  
0   1.0    NaN   3.0    1.0      NaN   1.0  2020-06-13 16:31:55  
1   1.0    NaN  13.0    NaN      NaN   6.0  2020-06-13 16:31:55  
2  13.0    1.0   3.0    NaN      7.0   1.0  2020-06-13 16:31:55

In [5]:
path = 'C:/Users/TL_Yu/Documents/GitHub/Facebook/Page/達特聖克/'
# df.to_pickle(path + 'Posts_達特聖克.plk')
# df.to_excel(path + 'Posts_達特聖克.xlsx')

## 抓留言

In [16]:
df = pd.read_pickle(path + 'Posts_達特聖克.plk')
print(df.shape)
df.head(1)

(779, 16)


NAME            PAGEID            POSTID                TIME  \
0  Dr.cink 達特聖克  1030601230318418  3274075312637654 2020-06-09 05:00:00   

                                             CONTENT  COMMENT_COUNT  \
0  說他是Cink的強力代表作不為過，皮膚科專業使用保濕精華 ✔️一上市不到2年銷售破300萬瓶...           66.0   

   DISPLAY_COMMENTS  SHARE_COUNT                      FEEDBACKTARGETID  ANGER  \
0              51.0          2.0  ZmVlZGJhY2s6MzI3NDA3NTMxMjYzNzY1NA==    NaN   

   HAHA   LIKE  LOVE  SORRY  WOW           UPDATETIME  
0   NaN  306.0   1.0    NaN  NaN  2020-06-09 12:39:33

In [6]:
import os
Comments = []
for i in os.listdir(path+'Comments/'):
    Comments.append(pd.read_pickle(path+'Comments/'+i))
Comments = pd.concat(Comments, ignore_index=True)
# Comments['LINK'] = Comments['AUTHOR'].apply(lambda x: 'https://www.facebook.com/'+x)
print(Comments.shape)
Comments.head(1)
# os.listdir(path)

(345019, 13)


NAME           AUTHOR              TIME     TEXT REPLIES  LIKECOUNT  \
0  蔡雅如  100023780771786  2020-01-23 21:39  鼠年行大運++       0          0   

             POSTID        COMMENTID PARENTCOMMENTAUTHORID PARENTCOMMENTID  \
0  1186798034858331  628524137721698                                         

  GENDER TYPENAME        UPDATETIME  
0      1    saved  2020-06-09 21:35

In [12]:
for i in os.listdir(path+'Comments/'):
    os.remove(path+'Comments/'+i)
Comments.to_pickle(path+'Comments/Comments.plk')

In [17]:
df = pd.merge(df,
              Comments.groupby('POSTID').agg('size').reset_index()['POSTID'],
              how = 'left',
              on = 'POSTID',
              indicator=True)
df = df.loc[df['_merge']=='left_only']
print(df.shape)
df.head(1)

(148, 17)


NAME            PAGEID            POSTID                TIME  \
330  Dr.cink 達特聖克  1030601230318418  3184918938219959 2020-05-01 14:47:18   

                                               CONTENT  COMMENT_COUNT  \
330  好的產品會說話！感謝Ｄ粉的真心推薦  火夯保養寵兒！現在人手必備 https://bit.l...            NaN   

     DISPLAY_COMMENTS  SHARE_COUNT FEEDBACKTARGETID  ANGER  HAHA  LIKE  LOVE  \
330               NaN          NaN              NaN    NaN   NaN   NaN   NaN   

     SORRY  WOW           UPDATETIME     _merge  
330    NaN  NaN  2020-06-09 12:39:33  left_only

In [18]:
for i, postid in enumerate(df['POSTID']):
    print(i, postid)
    try:
        df = Get_Comments(postid)
        df.to_pickle('C:/Users/TL_Yu/Documents/GitHub/Facebook/Page/達特聖克/Comments/' + postid + '.plk')
    except:
        print('ERROR: '+ postid)
# politic_comments = pd.concat(politic_comments, ignore_index=True)

0 3184918938219959
ERROR: 3184918938219959
1 3079969618714892
ERROR: 3079969618714892
2 3053655938012927
ERROR: 3053655938012927
3 3053490378029483
ERROR: 3053490378029483
4 3019556091422912
ERROR: 3019556091422912
5 3006711446040710
ERROR: 3006711446040710
6 178192453542709
(8515, 13)
7 2968289303216258
(30, 13)
8 567626657167843
(7176, 13)
9 2954818634563325
(35, 13)
10 474097786873106
(4967, 13)
11 2966056883439500
(32, 13)
12 2966084766770045
(18, 13)
13 2954809137897608
(33, 13)
14 2964557596922762
(27, 13)
15 2964346370277218
(34, 13)
16 191026698954275
(9902, 13)
17 2954882264556962
(28, 13)
18 2958054690906386
(43, 13)
19 2954773521234503
(40, 13)
20 181409239610692
(28645, 13)
21 2961569823888206
(32, 13)
22 2961562283888960
(25, 13)
23 2955002441211611
(34, 13)
24 2954879717890550
(31, 13)
25 2959806427397879
(109, 13)
26 2946327648743521
(17992, 13)
27 2958027040909151
(39, 13)
28 2954878304557358
(20, 13)
29 2959119584133230
(2039, 13)
30 2954748291237026
(45, 13)
31 293991

## 抓回覆

In [14]:
path = '/Users/TL_Yu/Documents/GitHub/Facebook/Page/Comments/'
Comments = pd.read_pickle(path+'Comments.plk')
print(Comments.shape)
Comments = Comments.loc[Comments['REPLIES']>=1,['POSTID', 'COMMENTID']]
print(Comments.shape)
Comments.head(3)

(5297286, 15)
(334930, 2)


POSTID         COMMENTID
12  1003803720005598  1003888113330492
29  1003803720005598  1004271453292158
30  1003803720005598  1003933163325987

In [15]:
import os
path = '/Users/TL_Yu/Documents/GitHub/Facebook/Page/Replies/'
Replies = []
for i in os.listdir(path):
    Replies.append(pd.read_pickle(path+i))
Replies = pd.concat(Replies, ignore_index=True)
print(Replies.shape)
Replies.head(1)

(1819293, 15)


NAME           AUTHOR              TIME TYPE ACCESSIBILITYLABEL  \
0  Bamboo Chang  100000011260501  2020-01-05 13:47                           

                TEXT REPLIES  LIKECOUNT             POSTID        COMMENTID  \
0  劉 カラメル 你多一個1啦XDDD       0          0  10156349212431065  468561237142440   

  PARENTCOMMENTAUTHORID                    PARENTCOMMENTID GENDER TYPENAME  \
0                        10156349212431065_155502049078804      1    saved   

         UPDATETIME  
0  2020-04-13 22:46

In [16]:
for i in os.listdir(path):
    os.remove(path+i)
Replies.to_pickle(path+'Replies.plk')

In [11]:
Replies = Replies.drop_duplicates(subset="PARENTCOMMENTID", keep='first')
Replies['PARENTCOMMENTID'] = Replies['PARENTCOMMENTID'].apply(lambda x: x.split('_',-1)[1])
Replies = Replies.loc[:,['PARENTCOMMENTID']]

In [12]:
Comments = pd.merge(Comments,
                    Replies,
                    how = 'left',
                    left_on='COMMENTID',
                    right_on='PARENTCOMMENTID',
                    indicator=True
                   )
Comments = Comments.loc[Comments['_merge']=='left_only']
print(Comments.shape)
Comments.head(1)
# 334918

(28497, 4)


POSTID        COMMENTID PARENTCOMMENTID     _merge
156  10155504378376065  456178991580288             NaN  left_only

In [13]:
path = '/Users/TL_Yu/Documents/GitHub/Facebook/Page/Replies/'
for num, postid, commentid in zip(list(range(Comments.shape[0])), Comments['POSTID'], Comments['COMMENTID']):
    print(num, postid, commentid, ': ', datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'), )
    try:
        df = Get_Replies(postid, commentid)
        df.to_pickle(path + postid + '_' + commentid + '.plk')
    except:
        print('ERROR: '+ postid)
# politic_comments = pd.concat(politic_comments, ignore_index=True)

0 10155504378376065 456178991580288 :  2020-04-13 22:22:46
ERROR: 10155504378376065
1 10155504378376065 118329032511657 :  2020-04-13 22:22:47
ERROR: 10155504378376065
2 10155506247796065 10155506251416065 :  2020-04-13 22:22:47
ERROR: 10155506247796065
3 10155506309761065 214070516155924 :  2020-04-13 22:22:47
ERROR: 10155506309761065
4 10155506309761065 500101677156599 :  2020-04-13 22:22:48
ERROR: 10155506309761065
5 10155506309761065 2214287275510470 :  2020-04-13 22:22:48
ERROR: 10155506309761065
6 10155506309761065 114510426235677 :  2020-04-13 22:22:48
ERROR: 10155506309761065
7 10155506309761065 564721433953541 :  2020-04-13 22:22:49
ERROR: 10155506309761065
8 10155506309761065 2036342943111639 :  2020-04-13 22:22:49
ERROR: 10155506309761065
9 10155506309761065 10155506314971065 :  2020-04-13 22:22:49
ERROR: 10155506309761065
10 10155506309761065 114513479568705 :  2020-04-13 22:22:50
ERROR: 10155506309761065
11 10155506309761065 101239310906610 :  2020-04-13 22:22:50
ERROR: 10

ERROR: 10155527801091065
96 10155527801091065 349256379196949 :  2020-04-13 22:23:19
ERROR: 10155527801091065
97 10155527801091065 349256379196949 :  2020-04-13 22:23:19
ERROR: 10155527801091065
98 10155535584321065 10155535588221065 :  2020-04-13 22:23:19
ERROR: 10155535584321065
99 10155535584321065 10155535599826065 :  2020-04-13 22:23:20
ERROR: 10155535584321065
100 10155535584321065 2237117699892086 :  2020-04-13 22:23:20
ERROR: 10155535584321065
101 10155537328521065 388397681704208 :  2020-04-13 22:23:20
ERROR: 10155537328521065
102 10155537328521065 125257858487406 :  2020-04-13 22:23:21
ERROR: 10155537328521065
103 10155537328521065 10155537389656065 :  2020-04-13 22:23:21
ERROR: 10155537328521065
104 10155537328521065 10155537329551065 :  2020-04-13 22:23:21
ERROR: 10155537328521065
105 10155537328521065 785336231810210 :  2020-04-13 22:23:22
ERROR: 10155537328521065
106 10155537328521065 10155537332396065 :  2020-04-13 22:23:22
ERROR: 10155537328521065
107 10155540818121065 

ERROR: 10155575945531065
190 10155575945531065 10155575974816065 :  2020-04-13 22:23:51
ERROR: 10155575945531065
191 10155575945531065 10155576129236065 :  2020-04-13 22:23:52
ERROR: 10155575945531065
192 10155575945531065 10155576216331065 :  2020-04-13 22:23:52
ERROR: 10155575945531065
193 10155575945531065 10155576091386065 :  2020-04-13 22:23:52
ERROR: 10155575945531065
194 10155575945531065 10155576039706065 :  2020-04-13 22:23:53
ERROR: 10155575945531065
195 10155575945531065 10155575987996065 :  2020-04-13 22:23:53
ERROR: 10155575945531065
196 10155575945531065 307976813191419 :  2020-04-13 22:23:54
ERROR: 10155575945531065
197 10155575945531065 731367310582530 :  2020-04-13 22:23:54
ERROR: 10155575945531065
198 10155579284626065 111612749900322 :  2020-04-13 22:23:54
ERROR: 10155579284626065
199 10155579284626065 597707504001502 :  2020-04-13 22:23:55
ERROR: 10155579284626065
200 10155579284626065 2424403724468628 :  2020-04-13 22:23:55
ERROR: 10155579284626065
201 101555792846

ERROR: 10155588536771065
285 10155588536771065 374331903126740 :  2020-04-13 22:24:26
ERROR: 10155588536771065
286 10155588536771065 10155588570621065 :  2020-04-13 22:24:26
ERROR: 10155588536771065
287 10155588536771065 718881398506208 :  2020-04-13 22:24:27
ERROR: 10155588536771065
288 10155588536771065 758645151170415 :  2020-04-13 22:24:27
ERROR: 10155588536771065
289 10155588736246065 10155588772791065 :  2020-04-13 22:24:27
ERROR: 10155588736246065
290 10155588736246065 10155588775801065 :  2020-04-13 22:24:28
ERROR: 10155588736246065
291 10155588736246065 10155588782576065 :  2020-04-13 22:24:28
ERROR: 10155588736246065
292 10155588736246065 10155588752851065 :  2020-04-13 22:24:28
ERROR: 10155588736246065
293 10155588736246065 10155588783081065 :  2020-04-13 22:24:29
ERROR: 10155588736246065
294 10155588736246065 10155588775051065 :  2020-04-13 22:24:29
ERROR: 10155588736246065
295 10155588736246065 10155588764461065 :  2020-04-13 22:24:30
ERROR: 10155588736246065
296 101555887

ERROR: 10155603339346065
380 10155603339346065 10155603360781065 :  2020-04-13 22:25:00
ERROR: 10155603339346065
381 10155603339346065 113981626339771 :  2020-04-13 22:25:00
ERROR: 10155603339346065
382 10155603339346065 147413326249914 :  2020-04-13 22:25:00
ERROR: 10155603339346065
383 10155603339346065 10155603491436065 :  2020-04-13 22:25:00
ERROR: 10155603339346065
384 10155603339346065 665745540506650 :  2020-04-13 22:25:01
ERROR: 10155603339346065
385 10155603339346065 119240315797418 :  2020-04-13 22:25:01
ERROR: 10155603339346065
386 10155603339346065 119240315797418 :  2020-04-13 22:25:01
ERROR: 10155603339346065
387 10155605012971065 788393968172989 :  2020-04-13 22:25:02
ERROR: 10155605012971065
388 10155605012971065 1267456263403366 :  2020-04-13 22:25:02
ERROR: 10155605012971065
389 10155605012971065 10155605039986065 :  2020-04-13 22:25:02
ERROR: 10155605012971065
390 10155605012971065 10155605041521065 :  2020-04-13 22:25:03
ERROR: 10155605012971065
391 1015560501297106

...

(2, 15)
27978 2494215614148921 2059274951048518 :  2020-04-14 02:58:03
(3, 15)
27979 2494215614148921 2059274951048518 :  2020-04-14 02:58:04
(3, 15)
27980 2494215614148921 2494217927482023 :  2020-04-14 02:58:05
(3, 15)
27981 2494215614148921 146631953068490 :  2020-04-14 02:58:06
(4, 15)
27982 2494215614148921 473799466717549 :  2020-04-14 02:58:06
(1, 15)
27983 2494215614148921 354249012142821 :  2020-04-14 02:58:07
(1, 15)
27984 2494215614148921 2338489613138514 :  2020-04-14 02:58:08
(1, 15)
27985 2494215614148921 466995267208846 :  2020-04-14 02:58:08
(2, 15)
27986 2494215614148921 149805336100101 :  2020-04-14 02:58:09
(2, 15)
27987 2494215614148921 186581995683370 :  2020-04-14 02:58:09
ERROR: 2494215614148921
27988 2494215614148921 210171683293049 :  2020-04-14 02:58:10
(3, 15)
27989 2494215614148921 332209191048259 :  2020-04-14 02:58:10
ERROR: 2494215614148921
27990 2494215614148921 394820754474570 :  2020-04-14 02:58:11
(1, 15)
27991 2494215614148921 2307959955967178 :  202

(2, 15)
28092 2494215614148921 1660904150720780 :  2020-04-14 02:59:22
(6, 15)
28093 2494215614148921 186575079017395 :  2020-04-14 02:59:22
(1, 15)
28094 2494215614148921 459367624904013 :  2020-04-14 02:59:23
(2, 15)
28095 2494215614148921 724500011327366 :  2020-04-14 02:59:24
(2, 15)
28096 2494215614148921 185143675834920 :  2020-04-14 02:59:25
(3, 15)
28097 2494215614148921 1396493420517080 :  2020-04-14 02:59:25
ERROR: 2494215614148921
28098 2494215614148921 2161795857263474 :  2020-04-14 02:59:25
(1, 15)
28099 2494215614148921 338331043779939 :  2020-04-14 02:59:26
(2, 15)
28100 2494215614148921 473801166717379 :  2020-04-14 02:59:27
(2, 15)
28101 2494215614148921 147774856298537 :  2020-04-14 02:59:27
(1, 15)
28102 2494215614148921 148078862936428 :  2020-04-14 02:59:28
(1, 15)
28103 2494215614148921 467001373874902 :  2020-04-14 02:59:29
ERROR: 2494215614148921
28104 2494215614148921 451561562242176 :  2020-04-14 02:59:29
ERROR: 2494215614148921
28105 2494215614148921 91226552

(9, 15)
28207 2494215614148921 148747859521476 :  2020-04-14 03:00:44
(1, 15)
28208 2494215614148921 2290017594439853 :  2020-04-14 03:00:44
(1, 15)
28209 2494215614148921 2107978232641745 :  2020-04-14 03:00:45
(1, 15)
28210 2494215614148921 492375104844756 :  2020-04-14 03:00:46
(2, 15)
28211 2494215614148921 2442598715971233 :  2020-04-14 03:00:46
(2, 15)
28212 2494215614148921 210172006626350 :  2020-04-14 03:00:47
(2, 15)
28213 2494215614148921 115678779729262 :  2020-04-14 03:00:48
(4, 15)
28214 2494215614148921 842922016043834 :  2020-04-14 03:00:49
(1, 15)
28215 2494215614148921 494041677805062 :  2020-04-14 03:00:50
(1, 15)
28216 2494215614148921 210172223292995 :  2020-04-14 03:00:50
(6, 15)
28217 2494215614148921 459274381580004 :  2020-04-14 03:00:51
(1, 15)
28218 2494215614148921 160050521790501 :  2020-04-14 03:00:52
(4, 15)
28219 2494215614148921 425072954757748 :  2020-04-14 03:00:53
(2, 15)
28220 2494215614148921 447928122711850 :  2020-04-14 03:00:53
(3, 15)
28221 249

(1, 15)
28321 2494215614148921 1120172438173105 :  2020-04-14 03:02:04
(3, 15)
28322 2494215614148921 2494230647480751 :  2020-04-14 03:02:05
(3, 15)
28323 2494215614148921 171225270581867 :  2020-04-14 03:02:06
(2, 15)
28324 2494215614148921 487168342074828 :  2020-04-14 03:02:06
ERROR: 2494215614148921
28325 2494215614148921 2494223940814755 :  2020-04-14 03:02:07
(2, 15)
28326 2494215614148921 378533389519636 :  2020-04-14 03:02:07
(4, 15)
28327 2494215614148921 102287131102998 :  2020-04-14 03:02:08
(1, 15)
28328 2494215614148921 934287610239857 :  2020-04-14 03:02:09
(1, 15)
28329 2494215614148921 148901966294403 :  2020-04-14 03:02:09
(3, 15)
28330 2494215614148921 439204556923936 :  2020-04-14 03:02:10
(1, 15)
28331 2494215614148921 378532342853074 :  2020-04-14 03:02:11
(3, 15)
28332 2494215614148921 115679336395873 :  2020-04-14 03:02:12
(2, 15)
28333 2494215614148921 146568363100371 :  2020-04-14 03:02:12
(8, 15)
28334 2494215614148921 156614415476772 :  2020-04-14 03:02:14
(

(8, 15)
28435 2494215614148921 145691153283530 :  2020-04-14 03:03:26
(1, 15)
28436 2494215614148921 100117041323519 :  2020-04-14 03:03:27
(5, 15)
28437 2494215614148921 473800523384110 :  2020-04-14 03:03:28
(4, 15)
28438 2494215614148921 2494218437481972 :  2020-04-14 03:03:28
(28, 15)
28439 2494215614148921 145686779950634 :  2020-04-14 03:03:30
(2, 15)
28440 2494215614148921 145689066617072 :  2020-04-14 03:03:31
(1, 15)
28441 2494215614148921 357061744987503 :  2020-04-14 03:03:32
(1, 15)
28442 2494215614148921 115678799729260 :  2020-04-14 03:03:32
(2, 15)
28443 2494215614148921 2494216084148874 :  2020-04-14 03:03:33
(6, 15)
28444 2494215614148921 186585682349668 :  2020-04-14 03:03:34
(3, 15)
28445 2494215614148921 149804336100201 :  2020-04-14 03:03:34
(1, 15)
28446 2494215614148921 100140681321155 :  2020-04-14 03:03:35
(2, 15)
28447 2494215614148921 2494222870814862 :  2020-04-14 03:03:36
(1, 15)
28448 2494215614148921 473809580049871 :  2020-04-14 03:03:37
(43, 15)
28449 2

# 除錯區

In [62]:
data

{'__ar': 1,
 'payload': None,
 'domops': [['replace',
   '#www_pages_reaction_see_more_unitwww_pages_home',
   False,
   {'__html': '<div class="_1xnd"><div class="_4-u2 _4-u8"><div class="_427x"><div class="_4-u2 mbm _4mrt _5jmm _5pat _5v3q _7cqq _4-u8" data-ft="&#123;&quot;fbfeed_location&quot;:36&#125;" data-fte="1" data-ftr="1" data-xt="AZUH6jD_qHHpbMuoh641ezcKjQ9VM-hsl80ZqqnnPGvyPgIjvlLzZA9AQFPJQ-Nw90m34u2r4M-N6wNOjm384RIp8hwAn5R5ECJKec1O75sYcRvG78yGKPEGULIhlIL82JMS9szIa7uSp4_iTLo9rHMxfD3B_ie51jY1zW6BUeFcwIW-KSjZSV2pbgDmIIY8b440dDXbwZflZHqu5tNpktIqLbvzd2c6UR6aXPV8-_CsnUPE2BLLHcfC1Hjip8CCJlb1Z4lxwL7G0ofZZnMjIQS3sfOHPs5whTZ3ikhSNwUoHpkkmUlF9U7_nMOW-JdcPJDwRA_gx27_rLSR2-l01qpT8PLWxmBYg1-YMup465fZkow-C9bI5lLV59aFcdXsqznG-CJTFESGaUtZnEcP-laaaw5F51_fv9muN1FMXcRJi2P4vUziOu0N2ZTOItR2uTs" data-xt-vimp="&#123;&quot;pixel_in_percentage&quot;:0,&quot;duration_in_ms&quot;:1,&quot;client_track_subsequent_impression&quot;:true,&quot;subsequent_gap_in_ms&quot;:60000,&quot;log_initial_nonviewable&

In [64]:
content_df = []
soup = BeautifulSoup(data['domops'][0][3]['__html'])
for i in soup.findAll('div', {'class':'userContentWrapper'}):
    # 因為會有鎖文的情況，當有鎖文的情況時就會無法讀取貼文內容
    try:
        CONTENT = i.find('div',{'data-testid':'post_message'}).text
    except:
        CONTENT = 'ERROR'
                
    try:
        TIME = datetime.datetime.fromtimestamp(int(i.find('abbr')['data-utime']))
    except:
        TIME = datetime.datetime.fromtimestamp(10000000000) # 有些是置入的廣告不會有時間，需要另外處理
    print(i.find('div',{'data-testid':'story-subtitle'})['id'])
    ndf1 = pd.DataFrame(data=[{'NAME':i.find('img')['aria-label'],
                               'TIME': TIME,
                               'CONTENT': CONTENT,
                               'PAGEID':re.findall('[0-9]{5,}', i.find('div',{'data-testid':'story-subtitle'})['id'])[0],
                               'POSTID':re.findall('[0-9]{5,}', i.find('div',{'data-testid':'story-subtitle'})['id'])[1]}],
                        columns=['NAME', 'PAGEID', 'POSTID', 'TIME', 'CONTENT'])
    content_df.append(ndf1)
pd.concat(content_df, ignore_index=True)

feed_subtitle_102764756435823;3142938992418369;;9
feed_subtitle_102764756435823;3140263572685911;;9
feed_subtitle_102764756435823;3133452746700327;;9
feed_subtitle_102764756435823;3130317673680501;;9
feed_subtitle_102764756435823;3129129397132662;;9
feed_subtitle_102764756435823;3128928237152778;;9
feed_subtitle_102764756435823;3126375564074712;;9
feed_subtitle_2517306091706125:5:0


IndexError: list index out of range